# Escape Gene Marker

In [24]:
import numpy as np

import numba
import pandas

import skimage
import skimage.io
import skimage.filters
import skimage.segmentation
import skimage.measure
import skimage.morphology
import skimage.feature
import bi1x

import matplotlib.pyplot as plt

import imageio

import os
import colorcet

import bokeh.io
import bokeh.plotting
import bokeh.palettes as bp
import bokeh.models

bokeh.io.output_notebook()

notebook_url = 'localhost:8888'

import max_int_projection
import auto_segmentation
import applying_man_seg
import xist_signal

Loading BokehJS ...

In [75]:
im_num = 11

directory = 'Data/test_ims/max_c2_TX_Spen_KO_WT_Xist_T4_Kdm_T1_Atrx_T6-{}.tiff'.format(im_num)
im = skimage.io.imread(directory)

'''fig, ax = skimage.filters.try_all_threshold(im, figsize=(20, 20), verbose=False)
plt.savefig('Data/test_ims/outputs/escape_gene_outputs/thresholding_comparisons/im{}_comparison.png'.format(im_num))
plt.show()'''

"fig, ax = skimage.filters.try_all_threshold(im, figsize=(20, 20), verbose=False)\nplt.savefig('Data/test_ims/outputs/escape_gene_outputs/thresholding_comparisons/im{}_comparison.png'.format(im_num))\nplt.show()"

In [76]:
def threshold_minimum(im):
    '''Takes an input of a numpy array of an image and returns the image
    filtered with the minimum filter threshold from scikit image.'''
    return skimage.filters.threshold_minimum(im)

In [77]:
directory = 'Data/test_ims/max_c2_TX_Spen_KO_WT_Xist_T4_Kdm_T1_Atrx_T6-01.tiff'
orig_im = skimage.io.imread(directory)

bokeh.io.show(bi1x.viz.imshow(orig_im))

In [78]:
thresh_im = threshold_minimum(orig_im)

thresh_im.shape

()

In [79]:
def boundary_segment_im(im, connectivity=10, mode='inner', buffer_size=10):
    '''Takes an input of an image as a numpy array and segments it using
    boundary segmentation.'''
    return auto_segmentation.mark_boundaries(im, 
                                             connectivity=connectivity, 
                                             mode=mode,
                                             buffer_size=buffer_size)

In [80]:
seg_im = boundary_segment_im(orig_im)

bokeh.io.show(bi1x.viz.imshow(seg_im))

In [81]:
def make_ims_2d(im_marker, im_dapi):
    '''Takes in two images in 3d and compresses them into 2D image. Takes in 
    two numpy arrays and returns two numpy arrays.'''
    labeled_im_marker = skimage.measure.label(im_marker)
    labeled_im_dapi = skimage.measure.label(im_dapi)
    
    # Making marker im 2D
    for region in skimage.measure.regionprops(labeled_im_marker):
        for coord in region.coords:
            (x, y, z) = coord
            labeled_im_marker[x][y][0] = 0
            labeled_im_marker[x][y][1] = 1
            labeled_im_marker[x][y][2] = 0
            
    for region in skimage.measure.regionprops(labeled_im_dapi):
        for coord in region.coords:
            (x, y, z) = coord
            labeled_im_dapi[x][y][0] = im_dapi[x][y][0]
            labeled_im_dapi[x][y][1] = 0
            labeled_im_dapi[x][y][2] = 0
    return (labeled_im_marker, labeled_im_dapi)

In [82]:
def apply_dapi_segmentation(im_marker, im_dapi):
    '''Takes an input of an image array as a numpy array segmented in the 
    DAPI channel and a numpy array segmented in another channel,
    both already labeled and compressed to 2D array and applies the DAPI 
    segmentation to the image. 
    
    Returns an image array as a numpy array.'''
    (labeled_im_marker, labeled_im_dapi) = make_ims_2d(im_marker, im_dapi)
            
    # Initialize dictionary for number of markers in cells
    num_markers_in_cell = {}
    
            
    # Make DAPI 2D and add Xist onto layer of RGB image
    for region in skimage.measure.regionprops(labeled_im_dapi):
        for coord in region.coords:
            (x, y, z) = coord
            labeled_im_dapi[x][y][0] = 1
            labeled_im_dapi[x][y][2] = 0
            if labeled_im_marker[x][y][1] == 1:
                labeled_im_dapi[x][y][1] = 1
    return labeled_im_dapi
    

In [83]:
def marker_areas(im_marker, im_dapi):
    '''Takes in an input of an image with the dapi and marker channels merged.
    
    Creates a distribution of the areas of the markers within a cell and only takes
    the brightest % based on the dist_thresh value'''
    
    (labeled_im_marker, labeled_im_dapi) = make_ims_2d(im_marker, im_dapi)
    merged_im = apply_dapi_segmentation(labeled_im_marker, labeled_im_dapi)
    area_dct = {}
    area_lst = []
    
    for dapi_region in skimage.measure.regionprops(labeled_im_dapi):
        dapi_coords = dapi_region.coords
        for dapi_coord in dapi_coords:
            (x_dapi, y_dapi, z_dapi) = dapi_coord
            for marker_region in skimage.measure.regionprops(labeled_im_marker):
                marker_coords = marker_region.coords
                i = 0
                for marker_coord in marker_coords:
                    (x_marker, y_marker, z_marker) = marker_coord
                    if labeled_im_marker[x_marker][y_marker][1] == 1:
                        if marker_coord in dapi_coords:
                            for i in range(1):
                                area = marker_region.area
                                centroid = marker_region.centroid
                                area_dct[centroid] = area
                                area_lst.append(area)
                                i += 1
    area_array = np.array(area_lst)
    return area_dct, area_array

The below contains code from the class I took 3rd term, Bi1x. Taught by Justin Bois, code written by TA Sarah Walton

In [84]:
def bs_sample(data):
    """Draw a bootstrap sample from array of flips"""
    return np.random.choice(data, replace=True, size=len(data))

In [85]:
def draw_bs_replicates(data, size=10000):
    '''Takes replicate samples of the dataset the number of times indicated by the 
    size. Returns a numpy array containing this data.'''
    bs_reps = np.empty(size)
    for i in range(size):
        bs_reps[i] = bs_sample(data)
    return bs_reps

In [86]:
def cutoff_value(data, percentile, size=10000):
    '''Computes the cutoff value based on the area_thresh. Takes only
    values above that threshold value for the percentile of data.'''
    rep_data = draw_bs_replicates(data, size=size)
    return np.percentile(data, percentile)

In [87]:
def run_cutoff_val_strict(data, percentile, time_run, size=10000):
    '''Takes an input of data in the form of a numpy array, a percentile cutoff
    point, number of bootstrap samples to draw and the number of times this has
    been run, increasing in strictness each time. Each time this runs, the percentile
    increases by .05. It cannot exceed 1.
    Returns a new stricter cutoff value for the cell.'''
    rep_data = draw_bs_replicates(data, size=size)
    strict_percentile = percentile + time_run*.05
    return np.percentile(data, strict_percentile)

In [102]:
def count_above_cutoff(centroid_dct, 
                       cell_centroid, 
                       data,
                       im_marker, 
                       im_dapi, 
                       area_dct, 
                       percentile, 
                       time_run=0, 
                       size=10000):
    '''Takes an input of an image array containing the data for image markers and 
    segmentation in the DAPI channel, an area dictionary, containing the centroids
    of regions as keys and the area as values, and the cutoff value for area produced
    through bootstrapping.
    
    Returns a count for each cell of the number of markers in each as a dictionary of 
    cell centroid and number of markers counted. 
    
    Reruns cutoff_val on cells with more than 2 markers with a stricter percentile.'''
    if time_run == 0:
        cutoff_val = cutoff_value(data, percentile, size=size)
    else:
        cutoff_val = run_cutoff_val_strict(data, percentile, time_run, size=size)
    marker_count = 0
    for marker_centroid in centroid_dct[cell_centroid]:
        if area_dct[marker_centroid] > cutoff_val:
            marker_count += 1
    if marker_count > 2:
        count_above_cutoff(data, percentile, time_run=time_run+1, size=size)
    return marker_count

In [89]:
def connect_markers_to_cells(im_dapi, area_dct):
    '''Takes an input of an image segmented in the DAPI channel and a dictionary of the
    centroids of different markers from a dictionary of their areas.
    
    Returns the dictionary of each cell centroid as a key and the centroids of the markers
    as a list for the values.'''
    centroid_dct = {}
    labeled_im_dapi = skimage.measure.label(im_dapi)
    for dapi_region in skimage.measure.regionprops(labeled_im_dapi):
        coords = dapi_region.coords
        area_centroid_lst = []
        for area_key in area_dct:
            if area_key in coords:
                area_centroid_lst.append(area_key)
            centroid_dct[dapi_region.centroid] = area_centroid_lst
    return centroid_dct

In [103]:
def run_per_cell(im_marker, im_dapi, area_dct, percentile, size=10000):
    '''Takes an input of a numpy array of an image in the marker channel and DAPI channel. 
    Also takes in an input of a dictionary of the areas of different markers that use the 
    centroid as the key and area as the value and the size of the number of bootstrap samples
    to be taken to produce the distribution.
    
    Returns a a dictionary of cell centroids and the number of markers in each.'''
    number_of_markers_dct = {}
    centroid_dct = connect_markers_to_cells(im_dapi, area_dct)
    for cell_centroid in centroid_dct:
        area_data_lst = []
        for marker_centroid in centroid_dct[cell_centroid]:
            area_data_lst.append(area_dct[marker_centroid])
        area_data_array = np.array(area_data_lst)
        marker_count = count_above_cutoff(centroid_dct, 
                                          cell_centroid, 
                                          area_data_array, 
                                          im_marker, 
                                          im_dapi, 
                                          area_dct, 
                                          percentile, 
                                          time_run=0, 
                                          size=size)
        print(marker_count)
        number_of_markers_dct[cell_centroid] = marker_count
    return number_of_markers_dct

In [104]:
def intron_markers(input_path, 
                   output_path,
                   marker_channel, 
                   dapi_channel,
                   percentile,
                   bootstrap_size=10000):
    '''Takes a path to a folder containing raw tiffs in the intron marker channel,
    a path to a folder containing corresponding dapi images that have been segmented,
    the channel that the marker and dapi is in. 
    
    Thresholds and applies boundary segmentation to the images in the marker channel. 
    Then, compresses the marker and dapi channels into one layer of an RGB image
    and combines them into a single image.'''
    im_dct = {}
    for marker_im in os.listdir(input_path):
        marker_im_path_name = marker_im.split('.')
        if len(marker_im_path_name) >= 2:
            
            # Check if image is a tiff and splitting name to get image details
            if marker_im_path_name[1] == 'tiff' or marker_im_path_name[1] == 'tif':
                marker_im_array = skimage.io.imread(input_path + '/' + marker_im)
                marker_im_path_lst = marker_im_path_name[0].split('/')
                marker_im_name = marker_im_path_lst[len(marker_im_path_lst)-1]
                marker_im_name_ind_lst = marker_im_name.split('_')
                marker_im_name_ind = marker_im_name_ind_lst[len(marker_im_name_ind_lst)-1]
                if marker_channel in marker_im_path_name[0]:
                    
                    # Finding cooresponding DAPI image for a given marker image
                    for dapi_im in os.listdir(input_path):
                        dapi_im_path_name = dapi_im.split('.')
                        if len(dapi_im_path_name) >= 2:
                            if dapi_im_path_name[1] == 'tiff' or dapi_im_path_name[1] == 'tif':
                                dapi_im_array = skimage.io.imread(input_path + '/' + dapi_im)
                                dapi_im_path_lst = dapi_im_path_name[0].split('/')
                                dapi_im_name_ind_lst = dapi_im_path_lst[len(dapi_im_path_lst)-1].split('_')
                                if dapi_channel in dapi_im_path_name[0]:
                                    if marker_im_name_ind in dapi_im_path_lst[len(dapi_im_path_lst)-1]:
                                        
                                        # Thresholding and segmenting the marker image
                                        marker_im_thresh = boundary_segment_im(marker_im_array)
                                        
                                        (marker_area_dct, marker_area_array) = marker_areas(marker_im_thresh, dapi_im_array)
                                        
                                        # Calculating the number of markers in each cell based on distribution
                                        number_of_markers_dct = run_per_cell(marker_im_thresh, 
                                                                            dapi_im_array, 
                                                                             marker_area_dct, 
                                                                             percentile, 
                                                                             size=bootstrap_size)
                                        im_dct[marker_im_name + '.tiff'] = number_of_markers_dct
    return im_dct
        
                                        

In [96]:
number_of_markers_dct = intron_markers('Data/test_ims/single_test_im/im', 
                                       'Data/test_ims/single_test_im/outputs',
                                       'c2', 
                                       'c3',
                                       .5)

99.0
99.0
99.0


In [105]:
number_of_markers_dct = intron_markers('Data/test_ims/marker_test_ims', 'Data/test_ims/outputs/marker_outputs', 'c2', 'c3', .5)

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


KeyboardInterrupt: 

In [ ]:
number_of_markers_dct